In [13]:
import pandas as pd
import numpy as np
import sklearn
import matplotlib.pyplot as plt
data= pd.read_csv(r"C:\Users\Rohit\Downloads\Dataset_Consumer.csv",encoding = "latin1")
data.head()

Unnamed: 0  Unnamed: 0.1                                    ID  Birth Year  \
0           3           130  7e4b2602-00d5-3d55-a76a-d7f328756802        1976   
1           4           343  159a1e9e-9c5f-3cb3-b596-f86cdd876311        1979   
2           5           352  436e1239-27b4-326a-8346-d945cdba5c3a        1975   
3           6           353  436e1239-27b4-326a-8346-d945cdba5c3a        1975   
4           7           354  436e1239-27b4-326a-8346-d945cdba5c3a        1975   

   Gender Flag  Skillset1 Weight  Skillset2 Weight City of profile  \
0            0          0.454135          0.340607   San Francisco   
1            1          0.305647          0.255897         Livonia   
2            1          0.265585          0.208511   San Francisco   
3            1          0.265585          0.208511   San Francisco   
4            1          0.265585          0.208511   San Francisco   

  Country of profile  Education        ...          s2-Product Management  \
0      United States          0        ...                              0   
1      United States          4        ...                              0   
2      United States          0        ...                              0   
3      United States          0        ...                              0   
4      United States          0        ...                              0   

  s2-Public Policy s2-Real Estate  s2-Retail and Fashion s2-Sales  \
0                0              0                      0        0   
1                0              0                      0        0   
2                0              0                      0        0   
3                0              0                      0        0   
4                0              0                      0        0   

  s2-Social Media and Communications s2-Software Engineering  \
0                                  0                       0   
1                                  0                       0   
2                                  0                       0   
3                                  0                       0   
4                                  0                       0   

  s2-Video and Film Production s2-Web Design s2-Web Development  
0                            0             0                  0  
1                            0             0                  0  
2                            0             0                  0  
3                            0             0                  0  
4                            0             0                  0  

[5 rows x 87 columns]

In [14]:
print(len(data[data['laid_off']==1]))
print(len(data[data['laid_off']==0]))

1147
12886


In [15]:
not_laid_off = data[data['laid_off'] == 0]
laid_off = data[data['laid_off'] == 1]
np.random.seed(101)
drop_indices = np.random.choice(not_laid_off.index, 11739, replace=False)
not_laid_off = not_laid_off.drop(drop_indices)

data = pd.concat([not_laid_off, laid_off])
print('Training data size after dropping excessive observations: ', data.shape)

Training data size after dropping excessive observations:  (2294, 87)


In [16]:
print(len(data[data['laid_off']==1]))
print(len(data[data['laid_off']==0]))

1147
1147


In [17]:
data['Birth Year'] = data['Birth Year'].astype(float)
data = data.dropna(subset=['Length'])

In [18]:
y = data['laid_off']
X = data.drop(['Unnamed: 0','Unnamed: 0.1','Start Date','End Date','Employees Affected','Company Name','Layoff Date','Industry','Role','Dept','ID','City of profile','Country of profile','Location','laid_off'],axis = 1)

data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2294 entries, 1 to 14032
Data columns (total 87 columns):
Unnamed: 0                                 2294 non-null int64
Unnamed: 0.1                               2294 non-null int64
ID                                         2294 non-null object
Birth Year                                 2294 non-null float64
Gender Flag                                2294 non-null int64
Skillset1 Weight                           2294 non-null float64
Skillset2 Weight                           2294 non-null float64
City of profile                            2167 non-null object
Country of profile                         2294 non-null object
Education                                  2294 non-null int64
Elite Institution                          2294 non-null int64
Start Date                                 2294 non-null object
End Date                                   2294 non-null object
Length                                     2294 non-null int64

In [19]:
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
parameters = {
    'n_estimators' : [10, 20, 40,60,80, 120]
}
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3,random_state=101)
Grid_RF = GridSearchCV(RandomForestClassifier(),parameters, cv = 5)
Grid_RF.fit(X_train, y_train)

GridSearchCV(cv=5, error_score='raise-deprecating',
       estimator=RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators='warn', n_jobs=None,
            oob_score=False, random_state=None, verbose=0,
            warm_start=False),
       fit_params=None, iid='warn', n_jobs=None,
       param_grid={'n_estimators': [10, 20, 40, 60, 80, 120]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring=None, verbose=0)

In [20]:
# best number of trees
def print_grid_search_metrics(gs):
    print ("Best score: %0.3f" % gs.best_score_)
    print ("Best parameters set:")
    best_parameters = gs.best_params_
    for param_name in sorted(parameters.keys()):
        print("\t%s: %r" % (param_name, best_parameters[param_name]))


In [21]:
print_grid_search_metrics(Grid_RF)

Best score: 0.815
Best parameters set:
	n_estimators: 120


In [22]:
#Using best hyperparameters to check testing accuracy

RF = RandomForestClassifier(n_estimators=120)
RF.fit(X_train, y_train)
RF.score(X_test,y_test)

0.8534107402031931

In [23]:
#Feature Importances
a=pd.DataFrame(X.columns,columns=['Feature'])
a['Importance Score']=pd.DataFrame(RF.feature_importances_, columns=['Importance Score'])
a=a.sort_values(by='Importance Score', ascending=False)

In [29]:
import collections
import pydotplus
import pydot

from sklearn.tree import DecisionTreeClassifier, export_graphviz
dot_data = export_graphviz(RF.estimators_[60],
                                feature_names=X_train.columns,
                                out_file=None,
                                filled=True,
                                rounded=True)
graph = pydot.graph_from_dot_data(dot_data)



graph[0].write_png('tree_consumer.png')

from IPython.display import Image
from IPython.core.display import HTML 
Image(r"C:\Users\Rohit\tree_consumer.png",width=1200,height=1200)